# Parallelized Solution of Large, 3D, Finite-Element Problems in Julia

Corbin Foucart, MechE

The focus of this project is to leverage the power of Julia and parallel computing to more efficiently solve large-scale 3D finite element ocean equations, augmenting a a pre-existing research code.

The important
background to the problem can be summarized as:

<ol>
  <li> The existing code is in Python, and is slow.</li>
  <li>Bottleneck (memory, time) is in solution of large linear system, solved by an LU factorization</li>
  <li>We would like to do better, in terms of both memory and computation time. </li>
  <li> PyJulia is a really great package for "cross language gymnastics", allows Julia to be called from Python and operate directly on Python data. </li>
</ol>  


For those who are interested, our code implements a Hybridizable Discontinuous Galerkin (HDG) solver (unimportant here). Let's think about the finite element part as a "black box", and focus instead on the linear system.

## Brief introduction to LU decomposition

<img src="img/wikiLU.png">
<div style='width: 600px; text-align: center;'>Image: Wikipedia</div>

For small, dense linear systems:
<ul>
  <li> Only factor once!</li>
  <li> Back substitution </li>
  <li> Robust, (pretty) quick </li>
  <li> Direct method </li>
</ul> 

Large, sparse linear systems:
<ul>
  <li> O(n^3) factor time </li>
  <li> Store n^2 entries (without monkey tricks) </li>
  <li> very bad on memory </li>
</ul> 

Summary: for the sizes of problems we would like to solve, LU factorization simply does not scale. Note the log scale below! Factor + 10 timesteps.
<img src="img/presLUisBad.png", width=800px>

 We need to use iterative solvers.

## The problem of matrix "compression"

The large linear system we would like to solve is Symmetric Positive Definite (SPD), but was not coded that way [asd].

<img src="img/presMatrixComp.png">

We would like to have the SPD version of matrix at our fingertips:
<ul>
  <li> Use CG iterative method</li>
  <li> Otherwise, more general iterative method (GM-RES, Bi-CGSTAB) which are more general, but can not make use of SPD information. </li>
</ul> 

## Attempt 1: brute-force compression

<ul>
  <li> Julia allows us to write new methods for existing types</li>
  <li> Let's write a method that operates on the CSC matrix directly to remove the rows and columns we don't want, leaving us with SPD matrix </li>
</ul> 

### results:

<img src="img/presMatCompisBad.png", width=800px>

Turning the non-SPD matrix into an SPD one dominates computation time. Why is this so bad?
<ul>
  <li> We can use BenchMarkTools to find out </li>
  <li> The culprit is deleteat!(), which must delete the entries in the data vector of the SparseMatrixCSC type; when user deletes data, the data must be shifted down, very expensive </li>
</ul> 

We need a new approach.

## Attempt 2: "ignore the garbage"

Julia lets us create a new type from SparseMatrixCSC, "HollowSparseMatrixCSC", which overloads the *, + operators, so that the rows and columns that break the SPD quality of the matrix are simply ignored!

Matrix compression time is now "O(0)". Tres bien!

### results:

<ul>
  <li> Performance until LU decomposition runs out of memory, which ends the test. </li>
  <li> The CG method continues to work up to ~$5*10^8$ DOF </li>
<li> at ~$5*10^8$ DOF, a different part in the Python code (not even the linear system!) becomes the memory bottleneck. </li>
</ul> 

Note that at the last test before LU craps out:
<ul>
  <li> LU takes around 2.5 hours to solve the problem </li>
  <li> CG method takes about 30 seconds, competitive with the substitution portion of LU! </li>
</ul> 

Lastly, note the power of multiple dispatch. Once I've overloaded the * operator for HollowSparseMatrixCSC type, the IterativeSolvers.jl solvers "just work" out of the box!


<img src="img/presIgnoreResults.png", width=800px>

### Lingering Doubt:
<ul>
  <li> We spent so much brainpower on making everything CG-friendly </li>
  <li> Why is GM-RES better? </li>
</ul> 

Answer: It isn't. Never converges to tolerance, ($1*10^{-10}$), quits early. Wrong, but really fast.


<img src="img/presRelRes.png", width=800px>



## A brief note on preconditioners

<ul>
    <li> Pre/post-multiply by simple matrix that approximates $A^{-1}$, for faster convergence </li>
  <li> More of an art than a science, since better approximations will take longer to multiply. </li>
  <li> Implemented some simple preconditioners since Julia we can define custom multiplication for them, turns out Jacobi is best.  </li>
  <li> Summary: Preconditioners are fickle.  </li>
</ul> 

### results:

<img src="img/presPCG.png">

## Parallelization

<ul>
    <li> For large linear systems, we can do even better </li>
  <li> We can distribute global linear system "action of A" over several cores using SharedArrays in Julia </li>
  <li> Once again, define a new type of matrix "ParHollowSparseCSC" that knows it's data is shared, and teach it how to *, + </li>
  <li> We can perform the matrix-vector multiplications for the CG iterations over many cores, instead of using only 1.  </li>
</ul> 

### results:

<img src="img/presParTime.png", width=800px>

## Application: Ocean modeling, play videos

## Closing thoughts

Julia made this (profiling, debugging, benchmarking, parallelizing) easy!

A change like this to the code would have taken way, way longer to implement in Python or C++.